In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/classi/ClassRF (1).pkl
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN141.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN177.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-MM68.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN136.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN161.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN155.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN133.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-MM81.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN176.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN168.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN154.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-Melt26.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-DN172.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-MM61.jpg
/kaggle/input/rgb-crop/CROP-RGB/rgb-melanoma-test/rgb-MM76.jpg
/kaggl

In [4]:
pip install gradio==3.14.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 16.2 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.3/75.3 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.7/45.7 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.6/70.6 kB 5.0 MB/s eta 0:00:00
  Created wheel for ffmpy: filename=ffmpy-0.3.0-py3-none-any.whl size=4711 sha256=92ce06a3d5c39ef58497e3878c9ddbe018e646d1110a1e7af66a0440f631746d
  Stored in directory: /root/.cache/pip/wheels/c0/96/80/1aeaaf27265398a7393b296714b84e51a7d00101f8a665a25a
Successfully built ffmpy
Note: you may need to restart the kernel to use updated packages.


In [8]:
import gradio as gr
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
from PIL import Image
import pickle
from tensorflow.keras.models import load_model


In [9]:
# Load the RGB to hyperspectral conversion model
converion_model = load_model('/kaggle/input/convmo/Conversion_model.h5')

# Load the cancer classification model
#cancer_model = pickle.load(open("/kaggle/input/classi/ClassRF (1).pkl", "rb"))

cancer_model = pickle.load(open("/kaggle/input/logistic/LRclass.pkl", "rb"))

In [10]:
def classify(rgb_image):
    img = Image.fromarray(rgb_image.astype('uint8'), 'RGB')
    img = img.resize((272, 512))
    arr = np.array(img).astype('float32') / 255.0
    new_size = (272, 512)
    resized_rgb_img = tf.image.resize(arr, new_size)
    resized_rgb_img = tf.reshape(resized_rgb_img, (272, 512, 3))
    resized_rgb_img = np.expand_dims(resized_rgb_img , axis=0)
    
  # Convert the RGB image to hyperspectral using your model
    hyperspectral_image = converion_model(resized_rgb_img)
    hyperspectral_image = tf.image.resize(hyperspectral_image, new_size)
    hyperspectral_image = tf.reshape(hyperspectral_image, (272, 512, 16))
    imgplot = hyperspectral_image.numpy().astype(np.float32)
    imgplot= imgplot.reshape(-1, 272*512*16)
    prediction = cancer_model.predict(imgplot)
    if np.argmax(prediction) == 0:
        x= "cancer"
    else:
        x="not a cancer"
    return x  

In [11]:
# Define the Gradio interface
#image_input = gr.inputs.Image()
output_label = gr.components.Label()
#output_label=["text"]
image_input = gr.components.Image()
gr.Interface(
    classify, 
    image_input, 
    output_label, 
    title="RGB to Hyperspectral Conversion and Cancer Classification", 
    description="Upload an RGB image and get a prediction of whether you have skin cancer or not."
).launch(share=True)

Running on local URL:  http://127.0.0.1:7860

Setting up a public link... we have recently upgraded the way public links are generated. If you encounter any problems, please report the issue and downgrade to gradio version 3.13.0
.
Running on public URL: https://3d8a5098-9d6d-46ab.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades (NEW!), check out Spaces: https://huggingface.co/spaces
